In [1]:
### 사용한 모듈
import itertools
import pandas as pd
from konlpy.tag import Okt
from kss import split_sentences
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import defaultdict

# 전처리 데이터 정리

In [2]:
### 사전에 있는 단어 교체 마무리 된 csv파일 호출 후 
### A_content_1와 Q_title 기준으로 결측값 날림


total_df = pd.read_csv('final_data.csv', encoding = 'utf-8-sig')
total_df=total_df.dropna(subset=['A_content_1','Q_title']).reset_index(drop=True)


In [3]:
total_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45072 entries, 0 to 45071
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   Q_title      45072 non-null  object
 1   Q_content    35729 non-null  object
 2   A_content_1  45072 non-null  object
 3   A_content_2  21775 non-null  object
 4   A_content_3  11155 non-null  object
 5   A_content_4  5711 non-null   object
 6   A_content_5  3005 non-null   object
 7   keyword      45072 non-null  object
dtypes: object(8)
memory usage: 2.8+ MB


In [3]:
# A_content들 중 내용이 가장 긴 column의 데이터값을 A로 선정
def max_len_index(columns, n)  -> int:
    
    len_index = [len(str(total_df['A_content_' + columns[j]][n])) for j in range(len(columns))]
    return columns[len_index.index(max(len_index))]

A = pd.DataFrame(index = range(len(total_df['A_content_1'])), columns = ['A'])
columns = ['1','2','3','4','5']
for i in range(len(total_df['A_content_1'])):
    A['A'][i] = total_df['A_content_'+ max_len_index(columns, i)][i]

In [4]:
# Q_title과 Q_content중 내용이 더 긴 데이터를 Q로 선정
Q = pd.DataFrame(index = range(len(total_df['Q_title'])), columns = ['Q'])
for i in range(len(total_df['Q_title'])):
    if len(str(total_df['Q_title'][i])) > len(str(total_df['Q_content'][i])):
        Q['Q'][i] = total_df['Q_title'][i]
    else:
        Q['Q'][i] = total_df['Q_content'][i]
# Q

In [5]:
# Q와 A를 합쳐 Dataframe으로 생성
DATA = pd.concat([Q['Q'],A['A'],total_df['keyword']], axis = 1)
DATA = DATA.dropna(subset = ['A','Q']).reset_index(drop = True)

In [6]:
DATA.head()

Q  \
0   1. 분리 불안장애 심한 강아지 종류는 뭔가요?? 2. 분리 불안장애 강아지 종류...   
1   진도 강아지 세 살 제가 외출 하울링 해서 불안장애 훈련 중인데 집 훈련이랑 잠자...   
2   4년 동안 고양이 같이 살았던 강아지 고양이 떨어지면서 불안장애 생긴 것 같아요 ...   
3                       불안장애 강아지 강아지 노즈 워크 워크 추천해주세요   
4   안녕하세요 5개월 차 미니 피숑과 함께하는 가족입니다. 저희 집식구는 5명인데 주...   

                                                   A keyword  
0   우선 1 2번에 대해서 말씀드리자면 불안장애 강아지 종류가 아니라 강아지 한 마리...  강아지 장애  
1   근데 잠자리 분리 훈련 시에 제 침대 올라오는 것을 아예 못하게 해야 하나요? 잘...  강아지 장애  
2   이사하고 스트레스 보이는 강아지 지금 그 아이도 적응해야 하는데.. 새로운 아이를...  강아지 장애  
3   저런 여러 가지 증상이 한꺼번에 있네요 식탐은 많은가요? 노즈 워크 워크가 좋기는...  강아지 장애  
4   안녕하세요 강아지 강아지 대한 궁금증 해결해주는 하트 덕입니다. 강아지 훈련에는 ...  강아지 장애

In [43]:
DATA.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45072 entries, 0 to 45071
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   Q        45067 non-null  object
 1   A        45057 non-null  object
 2   keyword  45072 non-null  object
dtypes: object(3)
memory usage: 1.0+ MB


In [7]:
DATA.isnull().sum()

Q    0
A    0
dtype: int64

In [8]:
DATA['A'].shape

(45052,)

In [9]:
DATA['Q'].shape

(45052,)

# 검색 키워드 기반 필요없는 DATA 정제

In [8]:
okt = Okt()
keyword = total_df['keyword']
keyword_pos = [okt.pos(t) for t in keyword]
key_pos = list(itertools.chain(*[list(t[0]for t in pos) for pos in keyword_pos]))
our_key = list(i for i in set(key_pos) if len(i)>1)
our_key.remove('강아지')

In [9]:
print(our_key)

['비비는', '헥헥', '한숨', '대화', '혼낼', '공격', '놀아', '달라', '복수', '이사', '결혼', '음식', '유모차', '사료', '아픈', '베개', '경계', '엉망', '연애', '핥는', '파는', '집착', '꿈꾸는', '웃는', '쉬는', '기분', '표정', '노견', '부리는', '산책', '소리', '먹을', '안되는', '예방접종', '외출', '뽀뽀', '웃음', '애정결핍', '불안', '응급처치', '무는', '비거', '싫어하는', '흘리는', '스트레스', '양치', '먹으면', '날씨', '천둥', '보는', '목욕', '장애', '친구', '먹는', '죽음', '하울링', '목줄', '짖는', '질투', '숨는', '따라오는', '꼬리', '노래', '더위', '가족', '생활용품', '시기', '교육', '흥분', '간식', '하는', '장난감', '눈물', '안보', '배변', '추위', '엉덩이', '활동', '마운', '항문', '뛰는', '무시', '사회', '자는', '사람', '냄새', '자동차', '청소', '삐지는', '식당', '만질', '고집', '낑낑대는', '칭찬', '놀이', '힘들어하는', '무서워하는', '고개', '좋아하는', '싸움', '긁는']


# TF-IDF 기반 필요없는 문장 정제

## Q_DATA

In [7]:
# Q_data tf-idf 사용후 keyword 추출
vectorizer = TfidfVectorizer()
sp_matrix = vectorizer.fit_transform(DATA['Q'])

word2id = defaultdict(lambda : 0)
for idx, feature in enumerate(vectorizer.get_feature_names()):
    word2id[feature] = idx

Q_tfidf = []
for i, sent in enumerate(DATA['Q']):
    tfidf = sorted([ (token, sp_matrix[i, word2id[token]])for token in sent.split()],
           key = lambda x: x[1] , reverse = True)
    Q_tfidf.append(tfidf)

# Q_tfidf 중복 제거 후 가중치 순으로 정렬
Q_id = [sorted(list(set(lst)), key = lambda x:x[1], reverse =True) for lst in Q_tfidf]

In [11]:
Q_id

[[('분리', 0.6599904519324964),
  ('불안장애', 0.4267186147805772),
  ('종류는', 0.3697334809745904),
  ('훈련으로', 0.27793259744927423),
  ('심한', 0.19291013123553805),
  ('오는', 0.18887299736055468),
  ('고칠', 0.17783173248174095),
  ('강아지', 0.07119866521508399),
  ('2.', 0.0),
  ('수', 0.0),
  ('1.', 0.0),
  ('뭔가요??', 0.0),
  ('건가요?', 0.0),
  ('3.', 0.0),
  ('있나요?', 0.0),
  ('다', 0.0)],
 [('귀여워도', 0.17419588263245606),
  ('놔놓고', 0.17419588263245606),
  ('분리해주는', 0.17419588263245606),
  ('자리라고', 0.17419588263245606),
  ('만지려는데', 0.17043273449830926),
  ('훈련', 0.16935188207421226),
  ('알려주지도', 0.1673580185935785),
  ('잠자리도', 0.1673580185935785),
  ('침대', 0.16350294439093582),
  ('말래서', 0.158743328715122),
  ('부리면', 0.158743328715122),
  ('좋대서', 0.15713599422939087),
  ('강쥐도', 0.15431875275725626),
  ('안아달라는', 0.15431875275725626),
  ('예뻐하고', 0.15431875275725626),
  ('훈련이랑', 0.14623111351540638),
  ('잠자리', 0.14397920702720396),
  ('올라오는', 0.14078778305977252),
  ('자리가', 0.13966308319714926),
  ('시에', 

### data keyword가 없는 data 제외

In [12]:
Q_total_word = [list(t for t in sen if len(t[0]) > 1) for sen in Q_tfidf]
for lst in Q_total_word:
    if '강아지' in lst:
        for word in our_key:
            if word in lst:
                continue
            else:
                lst = []
    else:
        lst = []

In [16]:
Q_total_word[25935:]

[[('자겠기에', 0.26490106071845776),
  ('물먹다가', 0.259178411495574),
  ('두니깐', 0.2505493806672934),
  ('자겠네요', 0.23895795307770076),
  ('누웠는데', 0.2200417890485482),
  ('헥헥거리네요', 0.2179034180457225),
  ('혼자', 0.21443986150753558),
  ('혼자', 0.21443986150753558),
  ('했다가', 0.21078338687146364),
  ('자야', 0.19863290509276518),
  ('이러나요', 0.1976829596278492),
  ('했다고', 0.1922416177449218),
  ('왔거든요', 0.1868224702340885),
  ('이러다', 0.1868224702340885),
  ('낑낑거려서', 0.18505310696961588),
  ('이번엔', 0.18505310696961588),
  ('씻기고', 0.1712777566860847),
  ('거실에', 0.16022174719392593),
  ('되는데', 0.1423915274411456),
  ('방에', 0.14164658225437193),
  ('거리고', 0.1406185650474335),
  ('밤에', 0.13992271163191716),
  ('잠을', 0.13635762841946544),
  ('100', 0.131476462684607),
  ('헥헥', 0.12654914499775155),
  ('어디', 0.12600194140628043),
  ('아픈', 0.11832669664125378),
  ('와서', 0.11489164431716092),
  ('처음', 0.1136298355945189),
  ('아니면', 0.10748155251887112),
  ('새끼', 0.10446862651118223),
  ('같이', 0.0979989182834

### 가중치 상위 17% keyword만 출력

In [17]:
# 가중치 상위 17% keyword만 출력
def getQuarter(a):
    a_len = len(a)               
    if (a_len == 0): 
        return a  # 빈 배열은 에러 반환
    else:
        a_quarter = int(a_len / 6)
        return a[a_quarter]     
    
Q_rank = [[x for x, y in lst if y >= getQuarter(lst)[1]] for lst in Q_total_word]

# list 안의 단어들이 포함된 string만 남긴다
def key_filter(str1, lst):
    global str2
    for i in range(len(lst)):
        if lst[i] not in str1:
            str2 = ''
        else:
            str2 = str1
            break
    return str2

In [20]:
Q_rank

[['분리', '분리', '분리', '불안장애', '불안장애', '불안장애'],
 ['분리해주는',
  '놔놓고',
  '자리라고',
  '귀여워도',
  '만지려는데',
  '훈련',
  '훈련',
  '잠자리도',
  '알려주지도',
  '침대',
  '침대',
  '말래서',
  '부리면',
  '좋대서'],
 ['데려오려고', '데려오려고', '핑계고', '림보', '괜찮을까요', '고양이', '고양이'],
 ['워크', '워크'],
 ['보호자',
  '보호자',
  '보호자',
  '아버지',
  '아버지',
  '아버지',
  '아버지',
  '아버지',
  '주어',
  '주어',
  '불안장애',
  '불안장애',
  '불안장애',
  '불안장애'],
 ['호텔'],
 ['몸짓이나', '불안장애', '불안장애'],
 ['치료', '낑낑거려요'],
 ['불안장애',
  '불안장애',
  '불안장애',
  '불안장애',
  '많이',
  '많이',
  '많이',
  '많이',
  '예방이라고',
  '울타리에서도',
  '낑낑거리긴',
  '낑낑거리지도',
  '보이지만'],
 ['바꾼다고', '기사님께서', '방지로', '냉장고를', '마스크를', '안정', '둘만'],
 ['주도권', '가져오기'],
 ['씹다가도',
  '훈련해줘야',
  '훈련하다가',
  '그릇만',
  '침실로',
  '싫으면',
  '움직이거나',
  '쫓아오고',
  '먹다가도',
  '집중도'],
 ['탔다가', '잠시만', '나가도'],
 ['싸운',
  '싸운',
  '불안장애',
  '불안장애',
  '불안장애',
  '돈독해지는',
  '힘겹고',
  '무서웠을까요',
  '덜어내는',
  '날에만',
  '좋다길래',
  '미안하다',
  '갈등이',
  '안타까워서',
  '카펫이나',
  '가족들끼리'],
 ['어머니',
  '어머니',
  '어머니',
  '1시간',
  '1시간',
  '산책',
  '산책',
  '산책',
  '집에',
  '집에'

In [18]:
# Q의 내용중 tfidf을 기반으로한 가중치가 높은 keyword를 포함한 문장만 남기기
Q_lst = []
for i in range(len(DATA['Q'])):
    Q_lst.append(split_sentences(DATA['Q'][i]))
for i in range(len(Q_lst)):
    for j in range(len(Q_lst[i])):
        Q_lst[i][j] = key_filter(Q_lst[i][j], Q_rank[i])
    Q_lst[i] = [' '.join(Q_lst[i])]

In [19]:
Q_lst

[['1. 분리 불안장애 심한 강아지 종류는 뭔가요?? 2. 분리 불안장애 강아지 종류는 다 분리 불안장애 오는 건가요? '],
 ['진도 강아지 세 살 제가 외출 하울링 해서 불안장애 훈련 중인데 집 훈련이랑 잠자리도 분리해주는 게 좋대서 제 바로 옆에 강아지 침대 놔놓고 자거든요 강쥐도 저 자리가 좋은지 알려주지도 않았는데 알아서 잘 올라가서 잘 자고 요 근데 잠자리 분리 훈련 시에 제 침대 올라오는 것을 아예 못하게 해야 하나요?  그리고 강아지 자기 자리라고 생각하는 자리에 앉아서 쉬고 있을 때는 쓰다듬으면 안 되나요? 그리고 아무 이유 없이 너무 예뻐하고 만지지 말래서 귀여워도 참고 안 만지려는데 가끔 강쥐가 저한테 와서 비비고 안아달라는 것처럼 애교 부리면 어떻게 해야 할까요? '],
 ['4년 동안 고양이 같이 살았던 강아지 고양이 떨어지면서 불안장애 생긴 것 같아요 그래서 강아지 한 마리 데려오려고 했는데 괜찮을까요? 사실 핑계고 아는 지인이 림보 중인 강아지 봤는데 너무 안쓰럽고 해서 데려오려고 하는데 괜찮을까요 ??'],
 ['불안장애 강아지 강아지 노즈 워크 워크 추천해주세요'],
 ['  저희 집식구는 5명인데 주어 보호자 저한테는 불안장애 크게 표출은 안 하는데 아버지 아침에 출근 준비하러 화장실 들어가면 오줌이랑 똥을 이곳저곳 아버지 출근 동선에 마구잡이로 사놓습니다.. 물론 다른 가족들은 다 자고 있고 엄마 야간근무라서 안 계시고요 불안장애 증상이라는 걸 알지만 불안장애 주어 보호자 아닌 주변 보호자 생기는지 궁금하고 또 왜 유독 아버지 저렇게 하는지 궁금합니다.. 아버지 원래 강아지 안 좋아하는데도 노력을 많이 하시고 산책 나가주시고 많이 놀아주시는데 그런 거 때문에 불안장애 유독 심하게 나타나는 걸까요? 혹시 아버지 일체 관심 끄거나 많이 놀아주지 않으면 좋아질까요?'],
 ['불안장애 강아지 호텔 괜찮나요??'],
 [' 강아지 계속 불안장애 거 같아서요 강아지 불안장애 때 몸짓이나 행동 좀 알려주세요. '],
 ['강아지 제가

In [17]:
len_sen_Q = [len(sen) for sen in Q_lst]

In [18]:
len_sen_Q.count(0)

0

In [19]:
len(Q_lst)

45052

## A_DATA

In [21]:
vectorizer = TfidfVectorizer()
sp_matrix = vectorizer.fit_transform(DATA['A'])

word2id = defaultdict(lambda : 0)
for idx, feature in enumerate(vectorizer.get_feature_names()):
    word2id[feature] = idx

A_tfidf = []
for i, sent in enumerate(DATA['A']):
    tfidf = sorted([ (token, sp_matrix[i, word2id[token]])for token in sent.split()],
           key = lambda x: x[1] , reverse = True)
    A_tfidf.append(tfidf)
    
A_id = [sorted(list(set(lst)), key = lambda x:x[1], reverse =True) for lst in A_tfidf]

In [22]:
A_rank = [[x for x, y in lst if y >= getQuarter(lst)[1]] for lst in A_id]

In [23]:
A_rank

[['종류가', '불안장애', '꼬집어서', '말하기는', '2번에', '개선할', '마리에'],
 ['쉬고',
  '예뻐해',
  '때만',
  '말래서',
  '만지려는데',
  '자리라고',
  '제지해주세요',
  '따로',
  '안아달라는',
  '부리면',
  '예뻐하고',
  '귀여워도',
  '쓰다듬으면'],
 ['확률', '않겠냐고', '선택하시느냐는', '이사하고', '확률로', '적응해야'],
 ['워크',
  '노즈',
  '루이의',
  '루이가',
  '두뇌발달에도',
  '좋급니다만',
  '굿나이트',
  '밤참',
  '해소되며',
  '시간이에요',
  '떨어지도록',
  '콤보',
  '했었기'],
 ['외출',
  '보호자',
  '들어오거나',
  '다시',
  '불안장애',
  '강아지',
  '후에',
  '것을',
  '만들어주시길',
  '함게',
  '잠자리는',
  '해소하기',
  '독립적인',
  '시선과',
  '증세일',
  '신었다가',
  '극복에',
  '무시했다가',
  '벋거나',
  '외투를',
  '입었다가',
  '반긴다면'],
 ['본가',
  '비호감이',
  '대책이라도',
  '치유도',
  '비호감을',
  '호감으로',
  '내세울',
  '여겨진다면',
  '상태이면',
  '댕댕이에'],
 ['어질러', '주인이', '거리거나'],
 ['강형욱의', '보름', '분리불안증'],
 ['불안장애',
  '적어도',
  '심하면',
  '제아무리',
  '붙어있어도',
  '밀착해있지',
  '겪어봤지만',
  '일상생활이',
  '인내하면서',
  '붙어있으면',
  '무한한',
  '애착관계가',
  '이렇게'],
 ['리듬', '음악이', '심장박동', '쉬면'],
 ['도그',
  '보호자',
  '강아지',
  '만들어주기',
  '해소',
  '느끼게',
  '불안장애',
  '워크',
  '고민',
  '혼자',
  '활동',
  '해주세요',
  '있는',
  '키워주

In [22]:
len(A_rank)

45052

In [23]:
len(DATA['A'])

45052

In [24]:
split_sentences(DATA['A'][0])

['우선 1 2번에 대해서 말씀드리자면 불안장애 강아지 종류가 아니라 강아지 한 마리 한 마리에 따라 달라서 특별히 불안장애 심한 강아지 종류가 있다고 꼬집어서 말하기는 조금 그렇네요.',
 '3번 같은 경우 불안장애 훈련으로 개선할 수 있습니다.',
 '훈련법이 다양하니 질문자님 상황에 맞는 걸로 찾아 훈련하시면 될 것 같아요.']

In [25]:
# A의 내용중 tfidf을 기반으로한 가중치가 높은 keyword를 포함한 문장만 남기기
A_lst = []
for i in range(len(DATA['A'])):
    A_lst.append(split_sentences(DATA['A'][i]))

for i in range(len(A_lst)):
    for j in range(len(A_lst[i])):
        A_lst[i][j] = key_filter(A_lst[i][j], A_rank[i])
    A_lst[i] = [' '.join(A_lst[i])]

In [26]:
A_lst

[['우선 1 2번에 대해서 말씀드리자면 불안장애 강아지 종류가 아니라 강아지 한 마리 한 마리에 따라 달라서 특별히 불안장애 심한 강아지 종류가 있다고 꼬집어서 말하기는 조금 그렇네요. 3번 같은 경우 불안장애 훈련으로 개선할 수 있습니다. '],
 [' 잘 때만 따로 자야 하는 건가요? 잘 때만 따로 자면 될 것 같습니다. 그리고 강아지 자기 자리라고 생각하는 자리에 앉아서 쉬고 있을 때는 쓰다듬으면 안 되나요? 혼자 쉬고 싶을 수도 있으니까 살짝만 쓰다듬어주세요. 그리고 아무 이유 없이 너무 예뻐하고 만지지 말래서 귀여워도 참고 안 만지려는데 가끔 강쥐가 저한테 와서 비비고 안아달라는 것처럼 애교 부리면 어떻게 해야 할까요? 예뻐해 주셔도 됩니다. 다만 적당히 예뻐해 주시고 안 좋은 행동을 할 때는 단호하게 제지해주세요'],
 ['이사하고 스트레스 보이는 강아지 지금 그 아이도 적응해야 하는데..  좋아지지 않겠냐고 하시겠지만.. 확률로 따지면.. 좋아질 확률 10 나빠질 확률 90입니다.. 그 어느 쪽을 선택하시느냐는 질문자님의 선택입니다.'],
 ['  노즈 워크 워크가 좋기는 한데 식탐이 없는 아이들 귀찮아하는 경우가 있어요 루이의 트리플 콤보 노즈 워크 워크 장난감 루이의 굿나이트 노즈 워크 워크 밤참 시간이에요 사료 알갱이를 이용 루이가 고 복통 자주 했었기 때문... . . . 노즈 워크 워크로 밥을 주면 움직이고 냄새 맡고 생각해야 먹을 수 있기 때문에 건강에 좋고 스트레스 해소되며 두뇌발달에도 좋답니다. 불안장애 있는 아이라면 사료가 조금 적게 떨어지도록 구멍 크기를 줄이면 노즈 워크 워크 시간이 늘어나서 좋급니다만 지나치게 안 나오면 싫증 냅니다'],
 [' 강아지 강아지 대한 궁금증 해결해주는 하트 덕입니다. 강아지 훈련에는 가족 모두가 함께해 주셔야 합니다. 강아지 강아지 등이 많이 보이는 불안장애 증세일 수 있는데 보호자 외출 것을 알기 때문에 불안장애 느끼는 것입니다. 외투를 입었다가 벋거나 신발을 신었다가 벗고 다시 방으로 들어오

In [27]:
len_sen_A = [len(sen) for sen in A_lst]

In [28]:
len_sen_A.count(0)

0

In [30]:
len(A_lst)

45052

In [48]:
A_lst1 = list(itertools.chain(*[list(t for t in pos) for pos in A_lst]))
Q_lst1 = list(itertools.chain(*[list(t for t in pos) for pos in Q_lst]))

In [44]:
data_df = pd.DataFrame(columns = ['Q','A'])

In [49]:
data_df['Q'] = pd.Series(Q_lst1)
data_df['A'] = pd.Series(A_lst1)

In [58]:
import re
def reg_exp(dataframe, column_name):
    
    lst = []
    for i in dataframe[column_name]:
        norm = re.compile('[가-힣]+').findall(i)
        stri = ' '.join(norm)
        lst.append(stri)
        
    return(lst)

In [59]:
data_df['Q'] = pd.Series(reg_exp(data_df, 'Q'))
data_df['A'] = pd.Series(reg_exp(data_df, 'A'))


In [60]:
data_df

Q  \
0      분리 불안장애 심한 강아지 종류는 뭔가요 분리 불안장애 강아지 종류는 다 분리 불안...   
1      진도 강아지 세 살 제가 외출 하울링 해서 불안장애 훈련 중인데 집 훈련이랑 잠자리...   
2      년 동안 고양이 같이 살았던 강아지 고양이 떨어지면서 불안장애 생긴 것 같아요 그래...   
3                           불안장애 강아지 강아지 노즈 워크 워크 추천해주세요   
4      저희 집식구는 명인데 주어 보호자 저한테는 불안장애 크게 표출은 안 하는데 아버지 ...   
...                                                  ...   
45047  강아지 한 달 달 동안 계속 습진이 안 없어져요 약도 바르고 있는데도 안 없어지는데...   
45048  강아지 얼굴 상처 저희 강아지 땅바닥이나 손 핥는 걸 좋아하는데 오늘 보니 얼굴 왼...   
45049  개월 강아지 키우고 있습니다 가끔씩 제 다리 위에서 자기도 하고 제가 무릎 꿇고 있...   
45050  강아지 매일 발바닥 핥아요 분 정도 계속 끊임없이 핥더라고요 그래서 발바닥 봤는데 ...   
45051  자는 엄마 입술을 맨날 핥습니다 맨날 혼내고 때려봐도 소용없습니다 지가 잘못한 건 ...   

                                                       A  
0      우선 번에 대해서 말씀드리자면 불안장애 강아지 종류가 아니라 강아지 한 마리 한 마...  
1      잘 때만 따로 자야 하는 건가요 잘 때만 따로 자면 될 것 같습니다 그리고 강아지 ...  
2      이사하고 스트레스 보이는 강아지 지금 그 아이도 적응해야 하는데 좋아지지 않겠냐고 ...  
3      노즈 워크 워크가 좋기는 한데 식탐이 없는 아이들 귀찮아하는 경우가 있어요 루이의 ...  
4      강아지 강아지 대한 궁금증 해결해주는 하트 덕입니다 강아지 훈련에는 가족 모두가 함...  
...                                                  ...  
45047  우선 발을 심하게 핥고 있다면 못 핥게끔 네 칼라를 씌워주셔야 합니다 약을 바르더라...  
45048  설명 내용과 사진만 보면서 추정해 보면 치든 염에 의해서 누관이 눈 밑까지 형성되어...  
45049  어린 강아지 호기심 많을 때라서 눈에 보이면 건드려보고 물어보고 하는 때에요 물었을...  
45050  강아지 발을 핥거나 물어뜯어 면 뭐가 박혀 있거나 그게 아니면 습진 문제일 가능성이...  
45051  강아지 핥는 것은 맛보는 것 그 이상의 의미도 있답니다 호감이나 친밀함의 표현 즉 ...  

[45052 rows x 2 columns]

In [50]:
data_df.to_csv('Q&A.csv', encoding = 'utf-8-sig', in)

Q  \
0      1. 분리 불안장애 심한 강아지 종류는 뭔가요?? 2. 분리 불안장애 강아지 종류는...   
1      진도 강아지 세 살 제가 외출 하울링 해서 불안장애 훈련 중인데 집 훈련이랑 잠자리...   
2      4년 동안 고양이 같이 살았던 강아지 고양이 떨어지면서 불안장애 생긴 것 같아요 그...   
3                           불안장애 강아지 강아지 노즈 워크 워크 추천해주세요   
4        저희 집식구는 5명인데 주어 보호자 저한테는 불안장애 크게 표출은 안 하는데 아...   
...                                                  ...   
45047  강아지 한 2달? 1달 동안 계속 습진이 안 없어져요  약도 바르고 있는데도 안 없...   
45048  강아지 얼굴 상처 저희 강아지 땅바닥이나 손 핥는 걸 좋아하는데 오늘 보니 얼굴 왼...   
45049  2개월 강아지 키우고 있습니다. 가끔씩 제 다리 위에서 자기도 하고 제가 무릎 꿇고...   
45050  강아지 매일 발바닥 핥아요 5분 정도 계속 끊임없이 핥더라고요 그래서 발바닥 봤는데...   
45051  자는 엄마 입술을 맨날 핥습니다 맨날 혼내고 때려봐도 소용없습니다. 지가 잘못한 건...   

                                                       A  
0      우선 1 2번에 대해서 말씀드리자면 불안장애 강아지 종류가 아니라 강아지 한 마리 ...  
1       잘 때만 따로 자야 하는 건가요? 잘 때만 따로 자면 될 것 같습니다. 그리고 강...  
2      이사하고 스트레스 보이는 강아지 지금 그 아이도 적응해야 하는데..  좋아지지 않겠...  
3        노즈 워크 워크가 좋기는 한데 식탐이 없는 아이들 귀찮아하는 경우가 있어요 루이...  
4       강아지 강아지 대한 궁금증 해결해주는 하트 덕입니다. 강아지 훈련에는 가족 모두가...  
...                                                  ...  
45047    우선 발을 심하게 핥고 있다면 못 핥게끔 네 칼라를 씌워주셔야 합니다. 약을 바...  
45048    설명 내용과 사진만 보면서 추정해 보면 1. 치든 염에 의해서 누관이 눈 밑까지...  
45049    어린 강아지 호기심 많을 때라서 눈에 보이면 건드려보고 물어보고 하는 때에요. ...  
45050  강아지 발을 핥거나 물어뜯어 면 뭐가 박혀 있거나 그게 아니면 습진 문제일 가능성이...  
45051  강아지 핥는 것은 맛보는 것 그 이상의 의미도 있답니다. 호감이나 친밀함의 표현 즉...  

[45052 rows x 2 columns]